In [1]:
# Converted from Jupyter notebook: piper-high.ipynb

# Cell 1
#@markdown ## <font color="ffc800"> **Google Colab Anti-Disconnect.** 🔌
#@markdown ---
#@markdown #### Avoid automatic disconnection. Still, it will disconnect after <font color="orange">**6 to 12 hours**</font>.

import IPython
js_code = '''
function ClickConnect(){
console.log("Working");
document.querySelector("colab-toolbar-button#connect").click()
}
setInterval(ClickConnect,60000)
'''
display(IPython.display.Javascript(js_code))

# Cell 2
#@markdown ## <font color="ffc800"> **Check GPU type.** 👁️
#@markdown ---
#@markdown #### A higher capable GPU can lead to faster training speeds. By default, you will have a <font color="orange">**Tesla T4**</font>.
!nvidia-smi

# Cell 3
!gdown 1YslZyyAvpNCfkfnpGGj2m-h0sIbtu4JZ

# CSV
!gdown 1gmuCnFCWQuqxkOBjFSymz-FyV_yoy9m1

# Cell 4
# import zipfile

# # For files you've uploaded to Colab
# with zipfile.ZipFile('/kaggle/working/dataset.zip', 'r') as zip_ref:
#     zip_ref.extractall('/kaggle/working/')

# Cell 5
#@markdown # <font color="ffc800"> **Install software.** 📦
#@markdown ---
#@markdown ####In this cell the synthesizer and its necessary dependencies to execute the training will be installed. (this may take a while)

# clone:
!git clone -q https://github.com/rmcpantoja/piper
%cd /kaggle/working/piper/src/python
!wget -q "https://raw.githubusercontent.com/coqui-ai/TTS/dev/TTS/bin/resample.py"
#!pip install -q -r requirements.txt
!pip install -q cython>=0.29.0 piper-phonemize==1.1.0 librosa>=0.9.2 numpy==1.26 onnxruntime>=1.15.0 pytorch-lightning
!pip install --upgrade gdown transformers
!bash build_monotonic_align.sh
# Useful vars:
use_whisper = True
print("Done!")

# Cell 6
# import shutil

# # Delete a folder and all its contents
# shutil.rmtree('/kaggle/working/dataset')

# Cell 7
# import shutil
# import os

# def remove_folder(folder_path):
#     """
#     Remove a folder and all its contents

#     Args:
#         folder_path: Path to the folder you want to remove
#     """
#     if os.path.exists(folder_path):
#         if os.path.isdir(folder_path):
#             try:
#                 # Remove directory and all its contents
#                 shutil.rmtree(folder_path)
#                 print(f"Successfully removed folder: {folder_path}")
#             except Exception as e:
#                 print(f"Error removing folder: {e}")
#         else:
#             print(f"The path exists but is not a directory: {folder_path}")
#     else:
#         print(f"Folder does not exist: {folder_path}")

# # Example usage
# remove_folder('/kaggle/working/dataset')

# Cell 8
#@markdown # <font color="ffc800"> **1. Extract dataset.** 🔥
#@markdown ---
#@markdown ####Important: the audios must be in <font color="orange">**wav format, (16000 or 22050hz, 16-bits, mono), and, for convenience, numbered. Example:**

#@markdown * <font color="orange">**1.wav**</font>
#@markdown * <font color="orange">**2.wav**</font>
#@markdown * <font color="orange">**3.wav**</font>
#@markdown * <font color="orange">**.....**</font>

#@markdown ---
import os
import wave
import zipfile
import datetime

def get_dataset_duration(wav_path):
    totalduration = 0
    for file_name in [x for x in os.listdir(wav_path) if os.path.isfile(x) and ".wav" in x]:
        with wave.open(file_name, "rb") as wave_file:
            frames = wave_file.getnframes()
            rate = wave_file.getframerate()
            duration = frames / float(rate)
            totalduration += duration
    wav_count = len(os.listdir(wav_path))
    duration_str = str(datetime.timedelta(seconds=round(totalduration, 0)))
    return wav_count, duration_str

%cd .
if not os.path.exists("/kaggle/working/dataset"):
    os.makedirs("/kaggle/working/dataset")
    os.makedirs("/kaggle/working/dataset/wavs")
%cd /kaggle/working/dataset
#@markdown ### Audio dataset path to unzip:
zip_path = "/kaggle/working/dataset.zip" #@param {type:"string"}
zip_path = zip_path.strip()
if zip_path:
    if os.path.exists(zip_path):
        if zipfile.is_zipfile(zip_path):
            print("Unzipping audio content...")
            !unzip -q -j "{zip_path}" -d /kaggle/working/dataset/wavs
        else:
            print("Copying audio contents of this folder...")
            fp = zip_path + "/."
            !cp -a "$fp" "/kaggle/working/dataset/wavs"
    else:
        raise Exception("The path provided to the wavs is not correct. Please set a valid path.")
else:
    raise Exception("You must provide with a path to the wavs.")

%cd /kaggle/working/dataset/wavs
audio_count, dataset_dur = get_dataset_duration("/kaggle/working/dataset/wavs")
print(f"Opened dataset with {audio_count} wavs with duration {dataset_dur}.")
%cd ..
#@markdown ---

# Cell 9
import shutil
import os

source_file = "/kaggle/working/metadata.csv"
destination_folder = "/kaggle/working/dataset"

# Create destination folder if it doesn't exist
os.makedirs(destination_folder, exist_ok=True)

# Get just the filename from the source path
filename = os.path.basename(source_file)

# Create the full destination path
destination_path = os.path.join(destination_folder, filename)

# Move the zip file to the destination
shutil.move(source_file, destination_path)

print(f"File moved from {source_file} to {destination_path}")

# Cell 10
# import shutil
# import os

# source_file = "/kaggle/working/wavs"
# destination_folder = "/kaggle/working/dataset/"

# # Create destination folder if it doesn't exist
# os.makedirs(destination_folder, exist_ok=True)

# # Get just the filename from the source path
# filename = os.path.basename(source_file)

# # Create the full destination path
# destination_path = os.path.join(destination_folder, filename)

# # Move the zip file to the destination
# shutil.move(source_file, destination_path)

# print(f"File moved from {source_file} to {destination_path}")

# Cell 11
# #@markdown # <font color="ffc800"> **2. Upload the transcript file.** 📝
# #@markdown ---
# #@markdown ####<font color="orange">**Important: the transcription means writing what the character says in each of the audios, and it must have the following structure:**

# #@markdown ##### <font color="orange">For a single-speaker dataset:
# #@markdown * wavs/1.wav|This is what my character says in audio 1.
# #@markdown * wavs/2.wav|This, the text that the character says in audio 2.
# #@markdown * ...

# #@markdown ##### <font color="orange">For a multi-speaker dataset:

# #@markdown * wavs/speaker1audio1.wav|speaker1|This is what the first speaker says.
# #@markdown * wavs/speaker1audio2.wav|speaker1|This is another audio of the first speaker.
# #@markdown * wavs/speaker2audio1.wav|speaker2|This is what the second speaker says in the first audio.
# #@markdown * wavs/speaker2audio2.wav|speaker2|This is another audio of the second speaker.
# #@markdown * ...

# #@markdown And so on. In addition, the transcript must be in a <font color="orange">**.csv or .txt format. (UTF-8 without BOM)**

# #@markdown ## Auto-transcribe with whisper if transcription is not provided.

# #@markdown **Note: If you don't upload any transcription files, the wavs will be transcribed using the whisper tool when you execute the next step. Then, the notebook will continue with the rest of the preprocessing if there are no errors. Although the Whisper tool has good transcription results, in my experience I recommend transcribing manually and uploading it from this cell, since a good TTS voice needs to be optimized to give even better results. For example, when transcribing manually you will be able to observe every detail that the speaker makes (such as punctuation, sounds, etc.), and capture them in the transcription according to the speaker's intonations.**


# #@markdown However, if you want to transcribe and review this transcription, you can use the individual notebooks:

# #@markdown * [English](http://colab.research.google.com/github/rmcpantoja/My-Colab-Notebooks/blob/main/notebooks/OpenAI_Whisper_-_DotCSV_(Speech_dataset_multi-transcryption_support)en.ipynb)
# #@markdown * [French](http://colab.research.google.com/github/rmcpantoja/My-Colab-Notebooks/blob/main/notebooks/OpenAI_Whisper_-_DotCSV_(Speech_dataset_multi-transcryption_support)fr.ipynb)
# #@markdown * [Spanish](http://colab.research.google.com/github/rmcpantoja/My-Colab-Notebooks/blob/main/notebooks/OpenAI_Whisper_-_DotCSV_(Speech_dataset_multi-transcryption_support)es.ipynb)

# #@markdown ---
# %cd "/kaggle/working/dataset"
# from google.colab import files
# !rm /kaggle/working/dataset/metadata.csv

# if os.path.exists("/kaggle/working/dataset/wavs/_transcription.txt"):
#   !mv "/kaggle/working/dataset/wavs/_transcription.txt" metadata.csv
# else:
#   listfn, length = files.upload().popitem()
#   if listfn != "metadata.csv":
#     !mv "$listfn" metadata.csv

# use_whisper = False
# %cd ..

# Cell 12
!pip install faster-whisper

# Cell 13
#@markdown # <font color="ffc800"> **3. Preprocess dataset.** 🔄
#@markdown ---
import os
import torch
from faster_whisper import WhisperModel
from tqdm import tqdm
from google import colab

#@markdown ### ☑️ Use Whisper to auto-transcribe?
#@markdown Uncheck this box if you already have a `metadata.csv` file.
run_whisper_transcription = False #@param {type:"boolean"}

if run_whisper_transcription:
    device = "cuda" if torch.cuda.is_available() else "cpu"
    print(f"Using device: {device}")

    def make_dataset(path, language):
        metadata = ""
        text = ""
        files = [f for f in os.listdir(path) if f.endswith(".wav")]
        assert len(files) > 0, "You don't have wavs uploaded either! Please upload at least one zip with the wavs in step 2."
        
        # This will create/overwrite the metadata file
        metadata_filepath = "/kaggle/working/dataset/metadata.csv"
        metadata_file = open(metadata_filepath, "w")
        
        whisper = WhisperModel("large-v3", device=device, compute_type="float16")
        for audio_file in tqdm(files):
            full_path = os.path.join(path, audio_file)
            segments, _ = whisper.transcribe(full_path, word_timestamps=False, language=language)
            for segment in segments:
                text += segment.text
            text = text.strip()
            text = text.replace('\n', ' ')
            # Use the filename without the 'wavs/' prefix for metadata
            metadata = f"wavs/{audio_file}|{text}\n"
            metadata_file.write(metadata)
            text = ""
        
        metadata_file.close() # Close the file to save changes
        print(f"Transcription complete. File saved to {metadata_filepath}")
        del whisper
        return True

#@markdown ### First of all, select the language of your dataset.
language = "Deutsch" #@param ["العَرَبِي", "Català", "Čeština", "Dansk", "Deutsch", "Ελληνικά", "English (British)", "English (U.S.)", "Español (Castellano)", "Español (Latinoamericano)", "Suomi", "Français", "Magyar", "Icelandic", "Italiano", "ქართული", "қазақша", "Lëtzebuergesch", "नेपाली", "Nederlands", "Norsk", "Polski", "Português (Brasil)", "Português (Portugal)", "Română", "Русский", "Српски", "Svenska", "Kiswahili", "Türkçe", "українська", "Tiếng Việt", "简体中文"]
#@markdown ---
# language definition:
languages = {
    "العَرَبِي": "ar",
    "Català": "ca",
    "Čeština": "cs",
    "Dansk": "da",
    "Deutsch": "de",
    "Ελληνικά": "el",
    "English (British)": "en",
    "English (U.S.)": "en-us",
    "Español (Castellano)": "es",
    "Español (Latinoamericano)": "es-419",
    "Suomi.": "fi",
    "Français": "fr",
    "Magyar": "hu",
    "Icelandic": "is",
    "Italiano": "it",
    "ქართული": "ka",
    "қазақша": "kk",
    "Lëtzebuergesch": "lb",
    "नेपाली": "ne",
    "Nederlands": "nl",
    "Norsk": "nb",
    "Polski": "pl",
    "Português (Brasil)": "pt-br",
    "Português (Portugal)": "pt-pt",
    "Română": "ro",
    "Русский": "ru",
    "Српски": "sr",
    "Svenska": "sv",
    "Kiswahili": "sw",
    "Türkçe": "tr",
    "українська": "uk",
    "Tiếng Việt": "vi",
    "简体中文": "zh"
}

def _get_language(code):
    return languages[code]

final_language = _get_language(language)
#@markdown ### Choose a name for your model:
model_name = "german_medium_voice" #@param {type:"string"}
#@markdown ---
# output:
#@markdown ### Choose the working folder: (recommended to save to Drive)

#@markdown The working folder will be used in preprocessing, but also in training the model.
output_path = "/kaggle/working/training" #@param {type:"string"}
output_dir = output_path+"/"+model_name
if not os.path.exists(output_dir):
  os.makedirs(output_dir)
#@markdown --
#@markdown ### Choose dataset format:
dataset_format = "ljspeech" #@param ["ljspeech", "mycroft"]
#@markdown ---
#@markdown ### Is this a single speaker dataset? Otherwise, uncheck:
single_speaker = True #@param {type:"boolean"}
if single_speaker:
  force_sp = " --single-speaker"
else:
  force_sp = ""
#@markdown ---
#@markdown ### Select the sample rate of the dataset:
sample_rate = "22050" #@param ["16000", "22050"]
#@markdown ---
# creating paths:
if not os.path.exists("/kaggle/working/audio_cache"):
    os.makedirs("/kaggle/working/audio_cache")
%cd /kaggle/working/piper/src/python
#@markdown ### Do you want to train using this sample rate, but your audios don't have it?
#@markdown The resampler helps you do it quickly!
resample = False #@param {type:"boolean"}
if resample:
  !python resample.py --input_dir "/kaggle/working/dataset/wavs" --output_dir "/kaggle/working/dataset/wavs_resampled" --output_sr {sample_rate} --file_ext "wav"
  !mv /kaggle/working/dataset/wavs_resampled/* /kaggle/working/dataset/wavs
#@markdown ---
# check transcription:
if run_whisper_transcription:
    print("Transcript file not found or user opted for transcription. Transcribing audios using Whisper...")
    make_dataset("/kaggle/working/dataset/wavs", final_language[:2])
    print("Transcription done! Pre-processing...")
else:
    print("Skipping automatic transcription. Using existing metadata.csv file...")

!python -m piper_train.preprocess \
  --language {final_language} \
  --input-dir /kaggle/working/dataset \
  --cache-dir "/kaggle/working/audio_cache" \
  --output-dir "{output_dir}" \
  --dataset-name "{model_name}" \
  --dataset-format {dataset_format} \
  --sample-rate {sample_rate} \
  {force_sp}
print("Preprocessing done!")

# Cell 14
#@markdown # <font color="ffc800"> **4. Settings.** 🧰
#@markdown ---
import json
import ipywidgets as widgets
from IPython.display import display
from google.colab import output
import os
import re
import glob
#@markdown ### <font color="orange">**Select the action to train this dataset: (READ CAREFULLY)**

#@markdown * The option to <font color="orange">continue a training</font> is self-explanatory. If you've previously trained a model with free colab, your time is up and you're considering training it some more, this is ideal for you. You just have to set the same settings that you set when you first trained this model.
#@markdown * The option to <font color="orange">convert a single-speaker model to a multi-speaker model</font> is self-explanatory, and for this it is important that you have processed a dataset that contains text and audio from all possible speakers that you want to train in your model.
#@markdown * The <font color="orange">finetune</font> option is used to train a dataset using a pretrained model, that is, train on that data. This option is ideal if you want to train a very small dataset (more than five minutes recommended).
#@markdown * The <font color="orange">train from scratch</font> option builds features such as dictionary and speech form from scratch, and this may take longer to converge. For this, hours of audio (8 at least) are recommended, which have a large collection of phonemes.

action = "finetune" #@param ["Continue training", "convert single-speaker to multi-speaker model", "finetune", "train from scratch"]
#@markdown ---
if action == "Continue training":
    checkpoints = glob.glob(f"{output_dir}/lightning_logs/**/checkpoints/last.ckpt", recursive=True)
    if len(checkpoints):
        last_checkpoint = sorted(checkpoints, key=lambda x: int(re.findall(r'version_(\d+)', x)[0]))[-1]
        ft_command = f'--resume_from_checkpoint "{last_checkpoint}" '
        print(f"Continuing {model_name}'s training at: {last_checkpoint}")
    else:
        raise Exception("Training cannot be continued as there is no checkpoint to continue at.")
elif action == "finetune":
    if os.path.exists(f"{output_dir}/lightning_logs/version_0/checkpoints/last.ckpt"):
        raise Exception("Oh no! You have already trained this model before, you cannot choose this option since your progress will be lost, and then your previous time will not count. Please select the option to continue a training.")
    else:
        ft_command = '--resume_from_checkpoint "/kaggle/working/pretrained.ckpt" '
elif action == "convert single-speaker to multi-speaker model":
    if not single_speaker:
        ft_command = '--resume_from_single_speaker_checkpoint "/kaggle/working/pretrained.ckpt" '
    else:
        raise Exception("This dataset is not a multi-speaker dataset!")
else:
    ft_command = ""

# Download German medium quality checkpoint for finetuning
if action == "convert single-speaker to multi-speaker model" or action == "finetune":
    print(f"Downloading German medium quality pretrained model for finetuning...")
    
    # Use the specific German checkpoint you requested
    german_checkpoint_url = "https://huggingface.co/datasets/rhasspy/piper-checkpoints/resolve/main/de/de_DE/thorsten/medium/epoch%3D3135-step%3D2702056.ckpt"
    
    print(f"Downloading German Thorsten medium checkpoint...")
    print("\033[93mDownloading pretrained model...")
    
    # Download using wget since it's a direct URL
    get_ipython().system(f'wget -q "{german_checkpoint_url}" -O "/kaggle/working/pretrained.ckpt"')
    
    if os.path.exists("/kaggle/working/pretrained.ckpt"):
        print("\033[93mGerman medium model downloaded successfully!")
        print("This model is based on the Thorsten German voice dataset and is optimized for medium quality (22.05kHz, 15-20M params)")
    else:
        raise Exception("Couldn't download the German pretrained model!")
else:
    print("\033[93mWarning: this model will be trained from scratch. You need at least 8 hours of data for everything to work decent. Good luck!")


<IPython.core.display.Javascript object>

Sun Aug 17 11:54:09 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 560.35.03              Driver Version: 560.35.03      CUDA Version: 12.6     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   48C    P8             10W /   70W |       1MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

Downloading...
From (original): https://drive.google.com/uc?id=1YslZyyAvpNCfkfnpGGj2m-h0sIbtu4JZ
From (redirected): https://drive.google.com/uc?id=1YslZyyAvpNCfkfnpGGj2m-h0sIbtu4JZ&confirm=t&uuid=4ed084bb-4863-421b-9f5b-3b1e3c56057e
To: /kaggle/working/dataset.zip
  0%|                                                | 0.00/198M [00:00<?, ?B/s]

  2%|▉                                      | 4.72M/198M [00:00<00:12, 15.3MB/s]

  9%|███▍                                   | 17.3M/198M [00:00<00:04, 42.2MB/s]

...

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╸ 38.6/38.6 MB 154.2 MB/s eta 0:00:01

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 38.6/38.6 MB 43.2 MB/s eta 0:00:00


/kaggle/working/piper/src/python
Skipping automatic transcription. Using existing metadata.csv file...


Preprocessing done!


German medium model downloaded successfully!
This model is based on the Thorsten German voice dataset and is optimized for medium quality (22.05kHz, 15-20M params)


In [2]:
#@markdown ### Choose batch size based on this dataset:
batch_size = 22 #@param {type:"integer"}
#@markdown ---

#@markdown ### Choose the quality for this model:

#@markdown * x-low - 16Khz audio, 5-7M params
#@markdown * medium - 22.05Khz audio, 15-20 params
#@markdown * high - 22.05Khz audio, 28-32M params
quality = "medium" #@param ["high", "x-low", "medium"]
#@markdown ---
#@markdown ### For how many epochs to save training checkpoints?
#@markdown The larger your dataset, you should set this saving interval to a smaller value, as epochs can progress longer time.
checkpoint_epochs = 5 #@param {type:"integer"}
#@markdown ---
#@markdown ### Interval to save best k models:
#@markdown Set to 0 if you want to disable saving multiple models. If this is the case, check the checkbox below. If set to 1, models will be saved with the file name epoch=xx-step=xx.ckpt, so you will need to empty Drive's trash every so often.
num_ckpt = 2 #@param {type:"integer"}
#@markdown ---
#@markdown ### Save latest model:
#@markdown This checkbox must be checked if you want to save a single model (last.ckpt). Saving a single model is applied only if num_ckpt is equal to 0. If so, the interval parameter of epochs to save is ignored, since the last model per epoch is saved; also, you won't have to worry about storage. Being equal to 1, last.ckpt will be saved, but another model (model_vVersion.ckpt, the latter takes into account the epoch range you set), so you would have to empty the trash often.

#@markdown **It's not recommended to use this option in extremely small datasets, since by saving the last model each epoch, this process will be very fast and the trainer will not be able to save the complete model, which would result in a corrupt last.ckpt.**
save_last = True # @param {type:"boolean"}
#@markdown ---
#@markdown ### Step interval to generate model samples:
log_every_n_steps = 1000 #@param {type:"integer"}
#@markdown ---
#@markdown ### Training epochs:
max_epochs = 10000 #@param {type:"integer"}
#@markdown ---

# Cell 15
#@markdown # <font color="ffc800"> **5. Run the TensorBoard extension.** 📈
#@markdown ---
#@markdown The TensorBoard is used to visualize the results of the model while it's being trained such as audio and losses.

%load_ext tensorboard
%tensorboard --logdir {output_dir}

# Cell 16
#@markdown # <font color="ffc800"> **6. Train.** 🏋️‍♂️
#@markdown ---
#@markdown ### Run this cell to train your final model!

#@markdown ---
#@markdown ### <font color="orange">**Disable validation?**
#@markdown By uncheck this checkbox, this will allow to train the full dataset, without using any audio files or examples as a validation set. So, it will not be able to generate audios on the tensorboard while it's training. It is recommended to disable validation on extremely small datasets.
validation = True #@param {type:"boolean"}
if validation:
    validation_split = 0.01
    num_test_examples = 1
else:
    validation_split = 0
    num_test_examples = 0
if not save_last:
    save_last_command = ""
else:
    save_last_command = "--save_last True "
get_ipython().system(f'''
python -m piper_train \
--dataset-dir "{output_dir}" \
--accelerator 'gpu' \
--devices 1 \
--batch-size {batch_size} \
--validation-split {validation_split} \
--num-test-examples {num_test_examples} \
--quality {quality} \
--checkpoint-epochs {checkpoint_epochs} \
--num_ckpt {num_ckpt} \
{save_last_command}\
--log_every_n_steps {log_every_n_steps} \
--max_epochs {max_epochs} \
{ft_command}\
--precision 32
''')

<IPython.core.display.Javascript object>

/usr/local/lib/python3.11/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


2025-08-17 11:58:26.926172: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered


E0000 00:00:1755431906.949509     202 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1755431906.956335     202 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


/usr/local/lib/python3.11/dist-packages/pytorch_lightning/trainer/call.py:282: Be aware that when using `ckpt_path`, callbacks used to create the checkpoint need to be provided during `Trainer` instantiation. Please add the following callbacks: ["ModelCheckpoint{'monitor': None, 'mode': 'min', 'every_n_train_steps': 0, 'every_n_epochs': 1, 'train_time_interval': None}"].


...

Epoch 3537:  40%|███▏    | 21/52 [00:39<00:58,  0.53it/s, v_num=0, step=41746.0]

Epoch 3537:  42%|███▍    | 22/52 [00:41<00:56,  0.53it/s, v_num=0, step=41748.0]

Epoch 3537:  44%|███▌    | 23/52 [00:43<00:54,  0.53it/s, v_num=0, step=41748.0]

Epoch 3537:  44%|███▌    | 23/52 [00:43<00:54,  0.53it/s, v_num=0, step=41750.0]

Epoch 3537:  46%|███▋    | 24/52 [00:45<00:53,  0.53it/s, v_num=0, step=41752.0]